In [2]:
import sys
sys.path.append("/home/mat/repos/gpu_monitor") 

In [2]:
from gpumon import nvidia_run, extract_and_print, extract
import asyncio
%load_ext autoreload
%autoreload 2

In [3]:
%%time
a=extract(nvidia_run())

CPU times: user 8 ms, sys: 4 ms, total: 12 ms
Wall time: 1.59 s


In [4]:
async def fetch():
    return extract(nvidia_run())

In [5]:
async def produce(sem, queue):
    while True:
        # produce an item
        message = await fetch(sem)
        await asyncio.sleep(0)
        # put the item in the queue
        await queue.put(message)

In [6]:
async def consume(queue):
    while True:
        # wait for an item from the producer
        res = await queue.get()
        print(res)
#         fail_probability = float(res['message'])
#         await update_plot(index, fail_probability)

        # Notify the queue that the item has been processed
        queue.task_done()

In [7]:
async def run():
    queue = asyncio.Queue()
    # create instance of Semaphore
    sem = asyncio.Semaphore(10)

    # Create client session that will ensure we dont open new connection
    # per each request.
    # schedule the consumer
    consumer = asyncio.ensure_future(consume(queue))
    await produce(sem, queue)
        
    # wait until the consumer has processed all items
    await queue.join()
    # the consumer is still awaiting for an item, cancel it
    consumer.cancel()

In [8]:
try:
    loop = asyncio.get_event_loop()
    loop.run_until_complete(run())
finally:
    print('Shutdown')
    loop.close()


Shutdown


TypeError: fetch() takes 0 positional arguments but 1 was given

In [10]:
import subprocess

In [12]:
interval_seconds=1

In [64]:
import select
import time

In [71]:
poller.poll??

In [80]:
proc.stdout.readlines??

In [138]:
from contextlib import contextmanager



In [280]:
import time

In [287]:
def parse_log(filename):
    with open(filename) as f:
        return parse_lines(list(f))

In [288]:
@contextmanager
def log_context(log_file, interval_seconds=1):
    print('Logging GPU in {}'.format(log_file))
    proc = subprocess.Popen(["nvidia-smi",
                             "dmon",
                             "-d", str(interval_seconds),
                             "-o", "DT",
                             "-f", log_file], stdout=subprocess.PIPE)
    yield lambda: parse_log(log_file)
    proc.terminate()
    

In [286]:
with log_context('test_gpu.txt') as a:
    print(a)
    time.sleep(5)
print(a)

Logging GPU in test_gpu.txt
eyeyeye
eyeyeye


In [144]:
%cat test_gpu.txt

#Date       Time        gpu   pwr  temp    sm   mem   enc   dec  mclk  pclk
#YYYYMMDD   HH:MM:SS    Idx     W     C     %     %     %     %   MHz   MHz
 20170901   10:19:52      0    40    41     0     0     0     0  2505   556
 20170901   10:19:52      1    40    38     0     0     0     0  2505   556
 20170901   10:19:52      2    41    45     0     0     0     0  2505   556
 20170901   10:19:52      3    41    48     0     0     0     0  2505   556
 20170901   10:19:53      0    40    41     0     0     0     0  2505   556
 20170901   10:19:53      1    40    38     0     0     0     0  2505   556
 20170901   10:19:53      2    41    45     0     0     0     0  2505   556
 20170901   10:19:53      3    42    48     0     0     0     0  2505   556
 20170901   10:19:54      0    40    41     0     0     0     0  2505   556
 20170901   10:19:54      1    40    38     0     0     0     0  2505   556
 20170901   10:19:54      2    41    45     0     0     0     0  2505   556
 20170901   

In [213]:
f=open('test_gpu.txt')

In [146]:
a=f.readline()

In [149]:
b=f.readline()

In [167]:
from datetime import datetime, time

In [182]:
convert_datetime = lambda x: datetime.strptime(x, '%Y%m%d')

In [186]:
convert_time = lambda x: datetime.strptime(x, '%H:%M:%S').time()

In [188]:
conversion_funcs = convert_datetime, convert_time, int, int, int, int, int, int, int, int, int

In [194]:
def parse_line(line_string):
    parsed_list = list((func(val) for func, val in zip(conversion_funcs, line_string.split())))
    return [datetime.combine(*parsed_list[:2])]+parsed_list[2:]

In [199]:
%time parse_line(b)

CPU times: user 0 ns, sys: 0 ns, total: 0 ns
Wall time: 87.5 µs


[datetime.datetime(2017, 9, 1, 10, 19, 52), 0, 40, 41, 0, 0, 0, 0, 2505, 556]

In [201]:
from itertools import islice

In [204]:
f.readlines??

In [218]:
msg_list = list(islice(f, 3))

In [ ]:
ate       Time        gpu   pwr  temp    sm   mem   enc   dec  mclk  pclk

In [247]:
gpu_headers = 'timestamp', 'gpu','pwr','temp','sm','mem','enc','dec','mclk','pclk'

In [258]:
header_dict = dict(zip(range(2, len(gpu_headers)+2),gpu_headers[1:]))

In [263]:
from itertools import filterfalse

In [275]:
def convert_to_df(msg_list):
    return (pd.DataFrame([line.split() for line in msg_list])
            .pipe(lambda x: x.assign(timestamp=pd.to_datetime(x[0]+' '+x[1])))
            .rename(columns=header_dict)
            .drop([0,1], axis=1))

In [276]:
def parse_lines(msg_list): 
    return convert_to_df(filterfalse(lambda x: x.startswith('#'), msg_list))

In [277]:
%time parse_lines(msg_list)

CPU times: user 4 ms, sys: 0 ns, total: 4 ms
Wall time: 4.11 ms


gpu pwr temp sm mem enc dec  mclk pclk           timestamp
0   0  40   41  0   0   0   0  2505  556 2017-09-01 10:19:52
1   1  40   38  0   0   0   0  2505  556 2017-09-01 10:19:52
2   2  41   45  0   0   0   0  2505  556 2017-09-01 10:19:52

0   2017-09-01 10:19:52
1   2017-09-01 10:19:52
2   2017-09-01 10:19:52
dtype: datetime64[ns]

In [241]:
h.rename(columns={0:'a', 1:'b'})

a         b  2   3   4  5  6  7  8     9   10
0  20170901  10:19:52  0  40  41  0  0  0  0  2505  556
1  20170901  10:19:52  1  40  38  0  0  0  0  2505  556
2  20170901  10:19:52  2  41  45  0  0  0  0  2505  556

In [236]:
h.eval('0 + 1')

1

In [229]:
pd.to_timestamp(h[1])

AttributeError: module 'pandas' has no attribute 'to_timestamp'

In [83]:

def nvidia_run_dmon_poll(output_func, interval_seconds=1, polling_timeout=1, polling_interval=0.2):
    proc = subprocess.Popen(["nvidia-smi", "dmon", "-d", str(interval_seconds), "-o", "DT"], stdout=subprocess.PIPE)

    poller = select.poll()
    poller.register(proc.stdout, select.POLLIN)

    while True:
        if poller.poll(polling_timeout):
            output_func(proc.stdout.readline())
        else:
            time.sleep(polling_interval)


In [88]:
a='aaa'

In [89]:
a.startswith('a')

True

In [134]:
class GpuAccumulator(object):
    def __init__(self):
        self._msg_list = []
        
    def __call__(self, msg):
        if msg.startswith(b'#'):
            print(msg)
        else:
            print(msg)#self._msg_list.append(msg.split())
    
    @property
    def messages(self):
        return self._msg_list

In [135]:
gpu_acum=GpuAccumulator()

In [137]:
nvidia_run_dmon_poll(gpu_acum)

b'#Date       Time        gpu   pwr  temp    sm   mem   enc   dec  mclk  pclk\n'
b'#YYYYMMDD   HH:MM:SS    Idx     W     C     %     %     %     %   MHz   MHz\n'
b' 20170901   10:10:25      0    40    32     0     0     0     0  2505   683\n'
b' 20170901   10:10:25      1    39    29     0     0     0     0  2505   556\n'
b' 20170901   10:10:25      2    40    34     0     0     0     0  2505   556\n'
b' 20170901   10:10:25      3    40    36     0     0     0     0  2505   556\n'
b' 20170901   10:10:26      0    77    34    25    12     0     0  2505  1025\n'
b' 20170901   10:10:26      1    39    29     0     0     0     0  2505   556\n'
b' 20170901   10:10:26      2    40    34     0     0     0     0  2505   556\n'
b' 20170901   10:10:26      3    40    36     0     0     0     0  2505   556\n'
b' 20170901   10:10:27      0    61    34    17    11     0     0  2505  1177\n'
b' 20170901   10:10:27      1    39    29     0     0     0     0  2505   556\n'
b' 20170901   10:10:27      

KeyboardInterrupt: 

In [129]:
import pandas as pd

In [130]:
pd.DataFrame(gpu_acum.messages)

0            1     2      3      4     5     6     7     8   \
0   b'20170901'  b'10:06:30'  b'0'  b'14'  b'31'  b'0'  b'0'  b'0'  b'0'   
1   b'20170901'  b'10:06:30'  b'1'  b'14'  b'28'  b'0'  b'0'  b'0'  b'0'   
2   b'20170901'  b'10:06:30'  b'2'  b'14'  b'33'  b'0'  b'0'  b'0'  b'0'   
3   b'20170901'  b'10:06:30'  b'3'  b'14'  b'35'  b'0'  b'0'  b'0'  b'0'   
4   b'20170901'  b'10:06:32'  b'0'  b'14'  b'31'  b'0'  b'0'  b'0'  b'0'   
5   b'20170901'  b'10:06:32'  b'1'  b'13'  b'28'  b'0'  b'0'  b'0'  b'0'   
6   b'20170901'  b'10:06:32'  b'2'  b'14'  b'33'  b'0'  b'0'  b'0'  b'0'   
7   b'20170901'  b'10:06:32'  b'3'  b'15'  b'35'  b'0'  b'0'  b'0'  b'0'   
8   b'20170901'  b'10:06:33'  b'0'  b'13'  b'31'  b'0'  b'0'  b'0'  b'0'   
9   b'20170901'  b'10:06:33'  b'1'  b'14'  b'28'  b'0'  b'0'  b'0'  b'0'   
10  b'20170901'  b'10:06:33'  b'2'  b'14'  b'33'  b'0'  b'0'  b'0'  b'0'   
11  b'20170901'  b'10:06:33'  b'3'  b'15'  b'35'  b'0'  b'0'  b'0'  b'0'   
12  b'20170901'  b'10:06:34'  b'0'  b'13'  b'31'  b'0'  b'0'  b'0'  b'0'   

        9       10  
0   b'324'  b'405'  
1   b'324'  b'405'  
2   b'324'  b'405'  
3   b'324'  b'405'  
4   b'324'  b'405'  
5   b'324'  b'405'  
6   b'324'  b'405'  
7   b'324'  b'405'  
8   b'324'  b'405'  
9   b'324'  b'405'  
10  b'324'  b'405'  
11  b'324'  b'405'  
12  b'324'  b'405'

In [63]:
def poll_process():
    proc = subprocess.Popen(["nvidia-smi", "dmon", "-d", str(interval_seconds), "-o", "DT"], stdout=subprocess.PIPE)
    while True:
        try:
            outs, errs = proc.communicate(timeout=1)
        except TimeoutExpired:

In [13]:
subprocess.run(["nvidia-smi", "dmon", "-d", str(interval_seconds), "-o", "DT"], stdout=subprocess.PIPE).stdout

KeyboardInterrupt: 

In [31]:
import asyncio




In [33]:
asyncio.create_subprocess_exec??

In [40]:


class async_generator(object):
    def __init__(self):
        self.process = asyncio.create_subprocess_exec("nvidia-smi", 
                                                            "dmon", 
                                                            "-d", 
                                                            str(interval_seconds), 
                                                            "-o", 
                                                            "DT",
                                                            stdout=asyncio.subprocess.PIPE)

    async def __aiter__(self):
        return self

    async def __anext__(self):
        stdout, stderr = await self.process.communicate()
        # Return stdout
        return stdout.decode().strip()
        

In [41]:
async def pess():
    async for i in async_generator():
        print(i)

In [42]:
try:
    loop = asyncio.get_event_loop()
    loop.run_until_complete(pess())
except:
    loop.close()

/anaconda/envs/py35/lib/python3.5/site-packages/ipykernel/__main__.py:5: RuntimeWarning: coroutine 'pess' was never awaited


In [43]:
import asyncio


async def outer():
    print('in outer')
    print('waiting for result1')
    result1 = await phase1()
    print('waiting for result2')
    result2 = await phase2(result1)
    return (result1, result2)


async def phase1():
    print('in phase1')
    return 'result1'


async def phase2(arg):
    print('in phase2')
    return 'result2 derived from {}'.format(arg)


In [62]:
loop.run_until_complete??

In [50]:
asyncio.get_event_loop??

In [56]:

event_loop = asyncio.get_event_loop()

In [ ]:


try:
    return_value = event_loop.run_until_complete(outer())
    print('return value: {!r}'.format(return_value))
finally:
    event_loop.close()

In [90]:
from gpumon import log_context
import time
%load_ext autoreload

%autoreload 2


The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [91]:
with log_context('test_gpu.txt') as log:
    time.sleep(10)

Logging GPU in test_gpu.txt


In [95]:
!cat test_gpu.txt

#Date       Time        gpu   pwr  temp    sm   mem   enc   dec  mclk  pclk
#YYYYMMDD   HH:MM:SS    Idx     W     C     %     %     %     %   MHz   MHz
 20170901   12:59:32      0    40    41     0     0     0     0  2505   556
 20170901   12:59:32      1    41    38     0     0     0     0  2505   556
 20170901   12:59:32      2    40    46     0     0     0     0  2505   556
 20170901   12:59:32      3    42    49     0     0     0     0  2505   556
 20170901   12:59:34      0    40    41     0     0     0     0  2505   556
 20170901   12:59:34      1    40    38     0     0     0     0  2505   556
 20170901   12:59:34      2    41    46     0     0     0     0  2505   556
 20170901   12:59:34      3    42    48     0     0     0     0  2505   556
 20170901   12:59:35      0    40    41     0     0     0     0  2505   556
 20170901   12:59:35      1    40    38     0     0     0     0  2505   556
 20170901   12:59:35      2    41    46     0     0     0     0  2505   556
 20170901   

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


In [110]:
df = log()

In [127]:
df.dropna(how='any')

gpu pwr temp sm mem enc dec  mclk pclk           timestamp
0      0  40   41  0   0   0   0  2505  556 2017-09-01 12:59:32
1      1  41   38  0   0   0   0  2505  556 2017-09-01 12:59:32
2      2  40   46  0   0   0   0  2505  556 2017-09-01 12:59:32
3      3  42   49  0   0   0   0  2505  556 2017-09-01 12:59:32
4      0  40   41  0   0   0   0  2505  556 2017-09-01 12:59:34
5      1  40   38  0   0   0   0  2505  556 2017-09-01 12:59:34
6      2  41   46  0   0   0   0  2505  556 2017-09-01 12:59:34
7      3  42   48  0   0   0   0  2505  556 2017-09-01 12:59:34
8      0  40   41  0   0   0   0  2505  556 2017-09-01 12:59:35
9      1  40   38  0   0   0   0  2505  556 2017-09-01 12:59:35
10     2  41   46  0   0   0   0  2505  556 2017-09-01 12:59:35
11     3  42   49  0   0   0   0  2505  556 2017-09-01 12:59:35
12     0  40   41  0   0   0   0  2505  556 2017-09-01 12:59:36
13     1  40   38  0   0   0   0  2505  556 2017-09-01 12:59:36
14     2  40   46  0   0   0   0  2505  556 2017-09-01 12:59:36
15     3  42   49  0   0   0   0  2505  556 2017-09-01 12:59:36
16     0  40   41  0   0   0   0  2505  556 2017-09-01 12:59:37
17     1  40   38  0   0   0   0  2505  556 2017-09-01 12:59:37
18     2  40   46  0   0   0   0  2505  556 2017-09-01 12:59:37
19     3  42   48  0   0   0   0  2505  556 2017-09-01 12:59:37
20     0  40   41  0   0   0   0  2505  556 2017-09-01 12:59:39
21     1  41   38  0   0   0   0  2505  556 2017-09-01 12:59:39
22     2  40   46  0   0   0   0  2505  556 2017-09-01 12:59:39
23     3  42   48  0   0   0   0  2505  556 2017-09-01 12:59:39
24     0  40   41  0   0   0   0  2505  556 2017-09-01 12:59:40
25     1  41   38  0   0   0   0  2505  556 2017-09-01 12:59:40
26     2  40   46  0   0   0   0  2505  556 2017-09-01 12:59:40
27     3  42   48  0   0   0   0  2505  556 2017-09-01 12:59:40
28     0  40   41  0   0   0   0  2505  556 2017-09-01 12:59:41
29     1  41   38  0   0   0   0  2505  556 2017-09-01 12:59:41
...   ..  ..  ... ..  ..  ..  ..   ...  ...                 ...
2580   3  41   49  0   0   0   0  2505  556 2017-09-01 13:06:21
2581   0  40   41  0   0   0   0  2505  556 2017-09-01 13:06:23
2582   1  40   38  0   0   0   0  2505  556 2017-09-01 13:06:23
2583   2  41   46  0   0   0   0  2505  556 2017-09-01 13:06:23
2584   3  42   48  0   0   0   0  2505  556 2017-09-01 13:06:23
2585   0  40   41  0   0   0   0  2505  556 2017-09-01 13:06:24
2586   1  41   38  0   0   0   0  2505  556 2017-09-01 13:06:24
2587   2  40   46  0   0   0   0  2505  556 2017-09-01 13:06:24
2588   3  41   49  0   0   0   0  2505  556 2017-09-01 13:06:24
2589   0  40   42  0   0   0   0  2505  556 2017-09-01 13:06:25
2590   1  40   38  0   0   0   0  2505  556 2017-09-01 13:06:25
2591   2  41   46  0   0   0   0  2505  556 2017-09-01 13:06:25
2592   3  42   48  0   0   0   0  2505  556 2017-09-01 13:06:25
2593   0  40   41  0   0   0   0  2505  556 2017-09-01 13:06:26
2594   1  40   38  0   0   0   0  2505  556 2017-09-01 13:06:26
2595   2  40   46  0   0   0   0  2505  556 2017-09-01 13:06:26
2596   3  41   48  0   0   0   0  2505  556 2017-09-01 13:06:26
2597   0  40   41  0   0   0   0  2505  556 2017-09-01 13:06:28
2598   1  40   38  0   0   0   0  2505  556 2017-09-01 13:06:28
2599   2  41   46  0   0   0   0  2505  556 2017-09-01 13:06:28
2600   3  42   48  0   0   0   0  2505  556 2017-09-01 13:06:28
2601   0  40   41  0   0   0   0  2505  556 2017-09-01 13:06:29
2602   1  40   38  0   0   0   0  2505  556 2017-09-01 13:06:29
2603   2  41   46  0   0   0   0  2505  556 2017-09-01 13:06:29
2604   3  41   49  0   0   0   0  2505  556 2017-09-01 13:06:29
2605   0  41   41  0   0   0   0  2505  556 2017-09-01 13:06:31
2606   1  41   38  0   0   0   0  2505  556 2017-09-01 13:06:31
2607   2  40   46  0   0   0   0  2505  556 2017-09-01 13:06:31
2608   3  42   48  0   0   0   0  2505  556 2017-09-01 13:06:31
2609   0  40   41  0   0   0   0  2505  556 2017-09-01 13:06:32

[2609 rows x 10 columns]

In [130]:
def extract(gpu_property, df)
    return (df.groupby(['timestamp', 'gpu'])[gpu_property]
       .first()
       .unstack(level=1)
       .ffill()
       .bfill())

gpu                   0   1   2   3
timestamp                          
2017-09-01 12:59:28  41  38  46  49
2017-09-01 12:59:29  41  38  46  48
2017-09-01 12:59:31  41  38  46  48
2017-09-01 12:59:32  41  38  46  49
2017-09-01 12:59:33  41  38  46  48
2017-09-01 12:59:34  41  38  46  48
2017-09-01 12:59:35  41  38  46  49
2017-09-01 12:59:36  41  38  46  49
2017-09-01 12:59:37  41  38  46  48
2017-09-01 12:59:39  41  38  46  48
2017-09-01 12:59:40  41  38  46  48
2017-09-01 12:59:41  41  38  46  48
2017-09-01 12:59:43  41  38  45  48
2017-09-01 12:59:44  41  38  46  49
2017-09-01 12:59:45  41  38  46  48
2017-09-01 12:59:46  41  38  46  48
2017-09-01 12:59:48  41  38  45  49
2017-09-01 12:59:49  41  38  46  48
2017-09-01 12:59:50  41  38  46  49
2017-09-01 12:59:51  42  38  46  49
2017-09-01 12:59:53  41  38  45  48
2017-09-01 12:59:54  41  38  46  49
2017-09-01 12:59:55  41  38  46  49
2017-09-01 12:59:57  41  38  46  48
2017-09-01 12:59:58  41  38  46  49
2017-09-01 12:59:59  41  38  46  49
2017-09-01 13:00:01  41  38  46  49
2017-09-01 13:00:02  41  38  46  49
2017-09-01 13:00:03  41  38  46  48
2017-09-01 13:00:05  41  38  46  48
...                  ..  ..  ..  ..
2017-09-01 13:05:54  41  38  46  49
2017-09-01 13:05:55  41  38  46  48
2017-09-01 13:05:56  41  38  46  49
2017-09-01 13:05:57  42  38  46  48
2017-09-01 13:05:59  41  38  46  48
2017-09-01 13:06:00  41  38  46  48
2017-09-01 13:06:01  42  38  46  49
2017-09-01 13:06:03  41  38  46  48
2017-09-01 13:06:04  42  38  46  48
2017-09-01 13:06:05  42  38  46  49
2017-09-01 13:06:07  41  38  46  49
2017-09-01 13:06:08  41  38  46  48
2017-09-01 13:06:09  41  38  46  48
2017-09-01 13:06:10  41  38  46  48
2017-09-01 13:06:12  41  38  46  48
2017-09-01 13:06:13  41  38  46  48
2017-09-01 13:06:15  41  38  46  48
2017-09-01 13:06:16  41  38  46  48
2017-09-01 13:06:17  41  38  46  48
2017-09-01 13:06:18  41  38  46  48
2017-09-01 13:06:20  41  38  46  48
2017-09-01 13:06:21  41  38  46  49
2017-09-01 13:06:23  41  38  46  48
2017-09-01 13:06:24  41  38  46  49
2017-09-01 13:06:25  42  38  46  48
2017-09-01 13:06:26  41  38  46  48
2017-09-01 13:06:28  41  38  46  48
2017-09-01 13:06:29  41  38  46  49
2017-09-01 13:06:31  41  38  46  48
2017-09-01 13:06:32  41  38  46  48

[326 rows x 4 columns]

In [106]:
f=open('test_gpu.txt')

In [306]:
len(f.readline())

76

In [298]:
!cat test_gpu.txt

#Date       Time        gpu   pwr  temp    sm   mem   enc   dec  mclk  pclk
#YYYYMMDD   HH:MM:SS    Idx     W     C     %     %     %     %   MHz   MHz
 20170901   12:26:38      0    40    41     0     0     0     0  2505   556
 20170901   12:26:38      1    40    38     0     0     0     0  2505   556
 20170901   12:26:38      2    41    46     0     0     0     0  2505   556
 20170901   12:26:38      3    42    48     0     0     0     0  2505   556
 20170901   12:26:39      0    40    41     0     0     0     0  2505   556
 20170901   12:26:39      1    40    38     0     0     0     0  2505   556
 20170901   12:26:39      2    41    46     0     0     0     0  2505   556
 20170901   12:26:39      3    41    48     0     0     0     0  2505   556
 20170901   12:26:40      0    40    41     0     0     0     0  2505   556
 20170901   12:26:40      1    41    38     0     0     0     0  2505   556
 20170901   12:26:40      2    40    46     0     0     0     0  2505   556
 20170901   

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


In [299]:
log()

OutOfBoundsDatetime: Out of bounds nanosecond timestamp: 2505-01-01 00:00:00